# Decision Tree Supervised Learning Model

In [171]:
#imports
import pandas as pd
from pathlib import Path
from sklearn import tree
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split
from sklearn.metrics import confusion_matrix, accuracy_score, classification_report
from kappa_score import qwkappa

In [143]:
 # Loading data
file_path = Path("wine_data/train.csv")
wine_train = pd.read_csv(file_path)
wine_test = pd.read_csv('wine_data/test.csv')
wine_train.head()

Id  fixed acidity  volatile acidity  citric acid  residual sugar  \
0   0            8.0              0.50         0.39             2.2   
1   1            9.3              0.30         0.73             2.3   
2   2            7.1              0.51         0.03             2.1   
3   3            8.1              0.87         0.22             2.6   
4   4            8.5              0.36         0.30             2.3   

   chlorides  free sulfur dioxide  total sulfur dioxide  density    pH  \
0      0.073                 30.0                  39.0  0.99572  3.33   
1      0.092                 30.0                  67.0  0.99854  3.32   
2      0.059                  3.0                  12.0  0.99660  3.52   
3      0.084                 11.0                  65.0  0.99730  3.20   
4      0.079                 10.0                  45.0  0.99444  3.20   

   sulphates  alcohol  quality  
0       0.77     12.1        6  
1       0.67     12.8        6  
2       0.73     11.3        7  
3       0.53      9.8        5  
4       1.36      9.5        6

In [144]:
wine_test.head()

Id  fixed acidity  volatile acidity  citric acid  residual sugar  \
0  2056            7.2             0.510         0.01             2.0   
1  2057            7.2             0.755         0.15             2.0   
2  2058            8.4             0.460         0.40             2.0   
3  2059            8.0             0.470         0.40             1.8   
4  2060            6.5             0.340         0.32             2.1   

   chlorides  free sulfur dioxide  total sulfur dioxide  density    pH  \
0      0.077                 31.0                  54.0  0.99748  3.39   
1      0.102                 14.0                  35.0  0.99586  3.33   
2      0.065                 21.0                  50.0  0.99774  3.08   
3      0.056                 14.0                  25.0  0.99480  3.30   
4      0.044                  8.0                  94.0  0.99356  3.23   

   sulphates  alcohol  
0       0.59      9.8  
1       0.68     10.0  
2       0.65      9.5  
3       0.65     11.7  
4       0.48     12.8

In [145]:
#take a look at the data types and number of values values 
print(wine_train.dtypes)
print("_______________________________________")
print('Number of values in the training data:')
wine_train['Id'].count() 

Id                        int64
fixed acidity           float64
volatile acidity        float64
citric acid             float64
residual sugar          float64
chlorides               float64
free sulfur dioxide     float64
total sulfur dioxide    float64
density                 float64
pH                      float64
sulphates               float64
alcohol                 float64
quality                   int64
dtype: object
_______________________________________
Number of values in the training data:


2056

Split the data and fit the decision tree model, then make predicitons 

In [151]:
# Split the data into training and testing sets
#features
X = wine_train.copy()
X.drop('quality', axis=1, inplace=True)

#target
y = wine_train['quality'].values.reshape(-1,1)

#saving test data set if used later on 
X_test = wine_test.copy()

#split train and test data
X_train, X_val, y_train, y_val = train_test_split(X, y, test_size = 0.2, random_state = 42) 

In [152]:
#create scaler instance 
scaler = StandardScaler()
#fit the data 
X_scaler = scaler.fit(X_train)

In [153]:
 # Scaling data
X_train_scaled = X_scaler.transform(X_train)
X_test_scaled = X_scaler.transform(X_val)

In [154]:
# Create decision tree classifier
model = tree.DecisionTreeClassifier(random_state = 42)

#fit model
model = model.fit(X_train_scaled, y_train)

#make our predictions
predicitons = model.predict(X_test_scaled)

Evaluate our Model

In [164]:
#evaluate our model with confustion matrix
cm = confusion_matrix(y_val, predictions)
cm_df = pd.DataFrame(
    cm, index=['Actual 3', 4, 5, 6, 7, 8], columns=['Predicted 3', 4, 5, 6, 7, 8]
)
# Calculating the accuracy score
acc_score = accuracy_score(y_val, predictions)

#display our matrix
print("Confusion Matrix")
display(cm_df)
print(f"Accuracy Score : {acc_score}")

Confusion Matrix


Predicted 3  4   5   6   7  8
Actual 3            0  0   1   1   0  0
4                   0  0   6   1   1  0
5                   1  4  97  49  15  3
6                   1  4  46  72  31  4
7                   0  4  11  27  21  6
8                   0  0   2   2   2  0

Accuracy Score : 0.46116504854368934


In [156]:
print("Classification Report")
print(classification_report(y_val, predictions))

Classification Report
              precision    recall  f1-score   support

           3       0.00      0.00      0.00         2
           4       0.00      0.00      0.00         8
           5       0.60      0.57      0.58       169
           6       0.47      0.46      0.46       158
           7       0.30      0.30      0.30        69
           8       0.00      0.00      0.00         6

    accuracy                           0.46       412
   macro avg       0.23      0.22      0.23       412
weighted avg       0.48      0.46      0.47       412



Vizualizing our Decision Tree

In [157]:
# Needed for decision tree visualization
import pydotplus
from IPython.display import Image

In [188]:
 # Create DOT data
dot_data = tree.export_graphviz(
    model, out_file=None, feature_names=X.columns, class_names=['0', '1', '2', '3', '4', '5'], filled=True
)


#Draw graph
graph = pydotplus.graph_from_dot_data(dot_data)

# Show graph
decision_tree = Image(graph.create_png())
decision_tree


dot: graph is too large for cairo-renderer bitmaps. Scaling by 0.850627 to fit



In [189]:
# Saving the tree as PNG
file_path = "decision_tree_train.png"
graph.write_png(file_path)

dot: graph is too large for cairo-renderer bitmaps. Scaling by 0.850627 to fit



True

In [187]:
#get kappa score
from kappa_score import qwkappa
import numpy as np
qwkappa(y_val.flatten()-3, predictions-3)

0.28828986243924126

In [184]:
#testing 
predictions -3

array([3, 4, 2, 2, 5, 2, 2, 5, 1, 2, 1, 3, 2, 3, 3, 3, 3, 3, 5, 2, 4, 4,
       2, 4, 3, 2, 2, 2, 2, 2, 2, 4, 3, 3, 2, 4, 4, 2, 2, 3, 4, 3, 3, 4,
       2, 3, 3, 2, 3, 4, 2, 2, 3, 2, 2, 1, 3, 4, 3, 3, 2, 2, 4, 3, 3, 4,
       4, 4, 2, 2, 1, 2, 2, 2, 3, 4, 3, 3, 4, 2, 3, 2, 5, 3, 2, 3, 3, 4,
       2, 3, 2, 1, 2, 3, 2, 3, 2, 2, 2, 4, 3, 3, 2, 3, 4, 2, 2, 2, 2, 2,
       5, 2, 3, 3, 2, 2, 2, 3, 3, 2, 4, 2, 3, 3, 2, 4, 2, 2, 2, 2, 2, 2,
       2, 3, 3, 3, 3, 3, 4, 3, 3, 2, 4, 3, 3, 3, 2, 2, 3, 3, 2, 3, 2, 3,
       2, 3, 2, 2, 2, 5, 2, 2, 4, 3, 4, 3, 1, 4, 2, 3, 2, 2, 2, 3, 3, 3,
       2, 4, 3, 3, 2, 2, 2, 4, 2, 5, 3, 4, 2, 2, 3, 3, 3, 4, 3, 2, 2, 3,
       4, 5, 3, 3, 2, 3, 2, 3, 4, 3, 3, 3, 4, 2, 4, 3, 4, 2, 3, 2, 3, 2,
       4, 2, 3, 2, 3, 2, 4, 2, 3, 2, 2, 2, 2, 3, 2, 2, 2, 2, 3, 2, 4, 3,
       3, 2, 2, 2, 3, 2, 4, 4, 2, 3, 4, 1, 3, 4, 2, 2, 2, 2, 4, 5, 3, 3,
       2, 3, 4, 3, 3, 4, 4, 3, 3, 3, 3, 4, 4, 0, 2, 2, 2, 2, 3, 5, 2, 2,
       3, 3, 3, 2, 3, 4, 2, 1, 3, 3, 2, 3, 3, 0, 5,